# Portfolio value estimation 

In this document a model striving to estimate the value generation potential of a portfolio of energy producing technologies, is build. 

![](IMG_0333.JPG)

## Model layout 

The model consists of a protfolio of tehcnologies. These technologies interact wiht the spot electricity market, the mFRR market and secondary markets such as the district heating and hydrogen markets. Currently only up regulation is considerd for mFRR and prices for DK1 are used. The portfolio technologies are model as being behind the same meeter.     

Electricity generated by portfolio technologies can either be consumed by other portfolio technologies without paing tarifs, or be sold to the spot makret, with tarifs added. Electricity can also be purchased from the spot market at the spot price plus tarifs. Any upragulation capacity available can be sold as mFRR capacity. Upregulation capacity includes both generators running below max capacity, or demand units such as boilers and electrolyzers running above zero load. 
Secondary products such as heat or hydrogen, generated by demand units are sold at fixed prices. 

Currently the model is allowed to spend 1M DKK on investements, and then seeks to maximize profit. 

Two very import simplifications made in this model are as follows:  
(1) the model has perfect foresight   
(2) model actions has no effect on market price

![](Schematic.png)




## To DO
- Nedregulering (special regulering)
- aFRR
- FCR
- Demand response

#### Imorts

In [1]:
import pandas as pd
from datetime import datetime
import numpy as np
from pyomo.environ import *
import pyomo
import plotly.graph_objects as go

### Data import

Data for 2017 is used, as this is the most recent year with all data available.


In [2]:
# Time range
T = pd.date_range('2019-01-01T00:00','2019-12-31T23:00',freq='H')

In [84]:
# Wind and solar availability 
df_capfactor = pd.read_csv('data/windcapacityfacotor.csv')
df_capfactor = df_capfactor.set_index(df_capfactor['HourUTC'])
# Regulating prices and volume
df_reg = pd.read_csv('data/regulating-power-dk1_2019_hourly_dkk.csv',sep=';',decimal=',')
df_reg = df_reg.set_index(pd.date_range('2019-01-01T00:00','2020-01-01T00:00',freq='H'))
# mFRR prices
df_mfrr=pd.read_csv('data/mfrrreservesdk1.csv',sep=',')
df_mfrr = df_mfrr.set_index(df_mfrr['HourUTC'])
# mFRR percent dispatch
df_mfrr_volume_fraction = pd.DataFrame(index=T,
             data=(df_reg['Volume up'][t.strftime('%Y-%m-%d %H:%M:%S')] / df_mfrr['mFRR_UpPurchased'][t.strftime("%Y-%m-%d %H:%M")] for t in T))
# FCR data 
df_fcr = pd.read_csv('data/fcrreservesdk1.csv')
df_fcr = df_fcr.set_index(df_fcr['HourUTC'])
# spot prices
df_spot=pd.read_csv('data/elspotprices.csv',sep=',')
df_spot = df_spot.set_index(df_spot['HourUTC'])



#### Data sources:   
Wind and solar data: view wind_data.ipynb ,   data sources [link](https://www.energidataservice.dk/dataset/electricitybalance) [link](https://www.energidataservice.dk/dataset/capacitypermunicipality/resource_extract/fa9e8860-a055-4bd4-aca3-260b7ad23564?page=7#resource-preview)  
Regulating prices [NordPool](https://www.nordpoolgroup.com/historical-market-data/)  
mFRR prices [EnergiNet mFRR data](https://www.energidataservice.dk/dataset/mfrrreservesdk1)  
FCR data [EnergiNet FCR data](https://www.energidataservice.dk/dataset/fcrreservesdk1/resource_extract/45433ada-5648-4d83-8eab-9d642db18ca5)   
spot prices [EnergiNet Spot data](https://www.energidataservice.dk/dataset/elspotprices/resource_extract/c86859d2-942e-4029-aec1-32d56f1a2e5d)  

The model is  created using the Pyomo library 

## Model Setings

Disable partitipation in the mFRR market  

Tech capacities controlls weather a technology is included or not. (0 - 1)

In [50]:
disable_mfrr = True
# Maximum allowable technology capacities. Select 1e3 if no limit 
tech_capacities = dict(Wind=1e3,Solar=1e3,Boiler=1e3,Electrolyzer=1e3,Battery=1e3)
#tech_capacities = dict(Wind=0,Solar=0,Boiler=0,Electrolyzer=1,Battery=0)

## Model

In [92]:
model = ConcreteModel()

All model parameters and variables that are indexed can be indexed with instances of the set $T$ containing all timestampts $t$ to be simulated (all hours of 2017), or by instances of the set $K$ containing all technologies included in the model $k$.

In [93]:
# This is the set refered to as K
technologies = ['Wind','Solar','Boiler','Electrolyzer','Battery']


## Portfolio specs

All portfolio specifications are variables to be optimized. Any given portfolio is given by the following specifications:  

Technology capacities $p_{k}$ [MW], for all technologies $k$ in $K$

Technology dispatch $g_{t,k}$ [MWh], for all timestamps $t$ in $T$ and all tehcnologies $k$ in $K$

The battery furthermore has two variables, which are storage capacity $h_s$ and state of charge $soc$


In [94]:
model.p = Var(technologies,domain=NonNegativeReals)
model.g = Var(T,technologies,domain=Reals)

model.h_s = Var(domain=NonNegativeReals)
model.soc = Var(T,domain=NonNegativeReals)

A binary variable is introduced to determine weather the model participates in the mFRR market or not. The variable is selected by the model. 

In [95]:
model.d_mfrr = Var(T,domain=Binary)

Technology efficiencies are also specified:  

Electrolyzer efficiency is set to 1, as the hydrogen price covers efficiency loss

Wind turbine capacity facotr: $n_{w,t}$ [%] (determined by wind availability)  
Electrolyser efficiency: $n_e$ [%]  
Electric boiler efficiency: $n_d$ [%]  
Battery charge/discharge effciency $n_s$ [%]  

In [96]:
model.n_w = Param(T,initialize=lambda model,t : df_capfactor['WindCapacityFactor'][t.strftime('%Y-%m-%d %H:%M')],domain=Reals)
model.n_pv = Param(T,initialize=lambda model,t : df_capfactor['SolarCapacityFactor'][t.strftime('%Y-%m-%d %H:%M')])
model.n_d = Param(initialize=1)
model.n_e = Param(initialize=1)
model.n_s = Param(initialize=0.96)

## Markets

Historic market data is used for the year 2017:

### mFRR market

When biding into the mFRR market, a price is recived per capacity made available $c_m$. If that capacity is activatet, given by the activation volume $v_r$, the regulating price $c_r$ is recieved for the regulated energy.

mFRR capacity price: $c_m,t$ [DKK/MW]  
Regulating price: $c_r,t$ [DKK/MWh]  
Regulating volume fraction: $v_r$ [%]  

### Spot market

In the spot market electricity can be sold to the spot price $c_s$. Tarifs are added to the purchased/sold energy.

Spot price: $c_s$ [DKK/MWh]  

### Secondary markets 
Heat and hydrogen are sold at fixed prices.  

District Heat price: $c_d$ [DKK/MWH], provided by Århus affald/varme

Hydrogen price: $c_h$ 388.9 [DKK/MWh el]  ~ 38.8 [DKK/kg hydrogen] *

\* 100 kWh el is used to generate 1 kg of hydrogen
  
## Tariffer 

#### Forbrug

Transmissionsnettarif: 53 [kr/MWh]  
Systemtarif: 44 [kr/MWh]  
Balancetarif for forbrug: 1.87 [kr/MWh]  

DSO afgift: 100 [kr/MWh]
  
Total: 198.87 [kr/MWh] 

#### Produktion 

Indfødningstarif: 3 [kr/MWh]  
Balancetarif for produktion 1.12 [kr/MWh]

Total: 4.12 [kr/MWh]

Kilde: [link](https://energinet.dk/El/Elmarkedet/Tariffer)

In [97]:
tarrif_sell = 4.12
tarrif_buy = 98.9 + 100
# DSO Tarrif

In [98]:
filter= [np.isnan(a) for a in np.array([df_spot['SpotPriceDKK'][t.strftime("%Y-%m-%d %H:%M")] for t in T])]
T[filter]

DatetimeIndex([], dtype='datetime64[ns]', freq='H')

In [99]:
df_fcr.head()

HourUTC            HourDK  FCR_DownExpected  \
HourUTC                                                                  
2020-04-14 21:00  2020-04-14 21:00  2020-04-14 23:00              20.0   
2020-04-14 20:00  2020-04-14 20:00  2020-04-14 22:00              20.0   
2020-04-14 19:00  2020-04-14 19:00  2020-04-14 21:00              20.0   
2020-04-14 18:00  2020-04-14 18:00  2020-04-14 20:00              20.0   
2020-04-14 17:00  2020-04-14 17:00  2020-04-14 19:00              20.0   

                  FCR_DownPurchased  FCR_DownPriceDKK  FCR_DownPriceEUR  \
HourUTC                                                                   
2020-04-14 21:00               21.0              66.0              8.84   
2020-04-14 20:00               21.0              66.0              8.84   
2020-04-14 19:00               21.0              66.0              8.84   
2020-04-14 18:00               21.0              66.0              8.84   
2020-04-14 17:00               21.0              66.0              8.84   

                  FCR_UpExpected  FCR_UpPurchased  FCR_UpPriceDKK  \
HourUTC                                                             
2020-04-14 21:00            20.0             22.2           189.0   
2020-04-14 20:00            20.0             22.2           189.0   
2020-04-14 19:00            20.0             22.2           189.0   
2020-04-14 18:00            20.0             22.2           189.0   
2020-04-14 17:00            20.0             22.2           189.0   

                  FCR_UpPriceEUR  
HourUTC                           
2020-04-14 21:00           25.32  
2020-04-14 20:00           25.32  
2020-04-14 19:00           25.32  
2020-04-14 18:00           25.32  
2020-04-14 17:00           25.32

In [100]:
# mFRR
model.c_m = Param(T, initialize=lambda model,t : df_mfrr['mFRR_UpPriceDKK'][t.strftime("%Y-%m-%d %H:%M")])
model.c_r = Param(T, initialize=lambda model,t : df_reg['Price up'][t.strftime("%Y-%m-%d %H:%M:%S")])
model.v_r = Param(T, initialize=lambda model,t : df_mfrr_volume_fraction[0][t.strftime('%Y-%m-%d %H:%M:%S')])
# FCR
model.c_fcr_up = Param(T,initialize=lambda model,t : df_fcr['FCR_UpPriceDKK'][t.strftime('%Y-%m-%d %H:%M')])
model.c_fcr_down = Param(T,initialize=lambda model,t : df_fcr['FCR_DownPriceDKK'][t.strftime('%Y-%m-%d %H:%M')])
# Spot
model.c_s = Param(T, initialize=lambda model,t : df_spot['SpotPriceDKK'][t.strftime("%Y-%m-%d %H:%M")])
# Hydrogen
hydrogen_price = np.mean(np.sort([model.c_s[t]  for t in T])[0:6000]) + tarrif_buy 
model.c_h = Param(T, initialize=lambda model,t : hydrogen_price  )
# Heating
dh_prices = [199,226,221,207,168,82,75,76,153,185,208,226]
model.c_d = Param(T, initialize =lambda model,t: dh_prices[int(t.strftime("%m"))-1])

## Investement constraint 

In order to constrain the model, it is only alowed to sped 1M DKK on portfolio technologies.

Wind: 545000 [kr/MW/year]   
Solar pv: 188000 [kr/MW/year]
Boiler: 33000 [kr/MW/year]   
Electrolyzer: 470000 [kr/MW/year]     
Battery: 284000 [kr/MW/year]
  
soruce: [Energistyrelsen Teknologikataloger](https://ens.dk/service/fremskrivninger-analyser-modeller/teknologikataloger)

In [101]:
capex = dict(Wind=545000,Solar=188000,Boiler=33000,Electrolyzer=470000,Battery=284000)
#capacities = dict(Wind=model.p_w,Solar=model.p_pv,Boiler=model.p_b,Electrolyzer=model.p_e,Battery=model.p_s)

total_capex = 0
for tech in technologies:
    total_capex = total_capex + capex[tech]*model.p[tech]
    


model.investement_limit = Constraint(expr = total_capex <= 1e6)

## Enable/Disable technologies

In [102]:
model.capacity_limit = Constraint(technologies,rule=lambda model,tech : model.p[tech]<= tech_capacities[tech])

## Disable mFRR

In [103]:
if disable_mfrr :
    model.mFRR_con = Constraint(T , rule=lambda model,t: model.d_mfrr[t]==0)

## Electrolyzer load hours constraint
The electrolyzer is constrained to run at least 6000 full load hours

In [104]:
model.electrolyzer_con = Constraint(expr = sum(model.g[t,'Electrolyzer'] * (1-model.d_mfrr[t]*model.v_r[t]) for t in T) >= 6000 * model.p['Electrolyzer'])
#model.electrolyzer_con2 = Constraint(expr = model.p['Electrolyzer'] == 1)

## Dispatch constraints

In order to ensure realistic operation, the dispatch of technologies must be limited not to surpass the installed capacity. 

$g_{t,k} \leq p_k$ for all $k$ and $t$ in $K$ and $T$ 

In [105]:
tech_lower_bound = dict(Wind=0,Solar=0,Boiler=0,Electrolyzer=0,Battery=-model.p['Battery'])
model.disp_const_high = Constraint(T,technologies, rule = lambda model,t,tech: model.g[t,tech]<=model.p[tech])
model.disp_const_low = Constraint(T,technologies, rule = lambda model,t,tech: model.g[t,tech]>= tech_lower_bound[tech] )

## Battery constraints

Batery state of charge $sos_1$ is given by the charge in the previous hour $sos_{t-1}$, plus the amount charged/discharged in the current hour $g_{s,t}$ multiplied with the storage efficiency $n_s$.   
$sos_t = sos_{t-1} + g_{s,t}*n_s $   

Battery state of charge cannot surpass the installed capacity.  
$sos_t \leq h_s$  

Battery storage capacity $h_s$ is given by the installed charge/discharge capacity $p_s$  
$p_s = h_s/3$

In [106]:
model.battery_constraint1 = Constraint(T,rule=lambda model,t: model.soc[t] == model.soc[T[np.where(T==t)[0][0]-1]] + model.g[t,'Battery']*model.n_s)
model.battery_constraint2 = Constraint(T,rule=lambda model,t: model.soc[t]<= model.h_s)
model.battery_constraint3 = Constraint(expr =  model.h_s == 3*model.p['Battery'])

## Tarrif constraint 
As the tarrif paids depends on weather energy is sold or bought, the sold/bought energy is calculated as seperate variables $E_{sold}$ and $E_{bough}$  
Mathematicaly this is defined as:  
$0 <= E_{sold} <= E_{max}\cdot d$  
$0 <= E_{bought} <= E_{max}\cdot (1-d) $   
$ E_{sold} - E_{bought} = \Delta E$  
$ d = \{0,1\}$  
$ \Delta E = g_w\cdot n_w - g_b - g_e $  
Where $\Delta E$ is the energy deficit and $d$ is a binary variable

In [107]:
bound = 1e3
model.E_sold = Var(T,domain=NonNegativeReals)
model.E_bought = Var(T,domain=NonNegativeReals)
model.d = Var(T,domain=Binary)

E_delta = lambda t: model.g[t,'Wind']*model.n_w[t] + model.g[t,'Solar']*model.n_pv[t] + model.g[t,'Battery'] - model.g[t,'Boiler'] - model.g[t,'Electrolyzer']

model.con1 = Constraint(T, rule= lambda model,t : model.E_sold[t] - model.E_bought[t] == E_delta(t))
model.con2 = Constraint(T, rule=lambda model,t: model.E_sold[t] <= bound*model.d[t])
model.con3 = Constraint(T, rule=lambda model,t: model.E_bought[t] <= bound*(1-model.d[t]))

# Objective function

The objective of the model is to maximize profit.

### Revenues 

Revenue generated in the markets are calculated individually.  

Spot market revenue: $R_{spot} = \sum_t E_{sold,t} \cdot (c_{s,t} + tarrif_{sell} ) - E_{bought,t} \cdot (c_{s,t} + tarrif_{buy} )  $

mFRR market revenue: $R_{mfrr} = \sum_t P_{mfrr,t} \cdot c_{m,t} + P_{mfrr,t} v_{r,t} c_{r,t} $

Hydrogen regvenue: $R_h = \sum_t g_{e,t} * c_h$

District heating revenue: $R_{dh} = \sum_t g_{b,t} * c_d $

### Objective function

Maximize $ p = R_{spot} + R_{mfrr} + R_h + R_{dh} $

In [66]:
R_spot = lambda t: model.E_sold[t]*(model.c_s[t] + tarrif_sell) - model.E_bought[t]*(model.c_s[t]+tarrif_buy) 

P_mfrr = lambda t : model.g[t,'Boiler'] + model.g[t,'Electrolyzer'] + (model.p['Wind']-model.g[t,'Wind'])*model.n_w[t]

R_mfrr = lambda t: model.d_mfrr[t] *(P_mfrr(t)*model.c_m[t] + P_mfrr(t)*model.v_r[t]*model.c_r[t])
#R_mfrr = lambda t:0*(P_mfrr(t)*model.c_m[t] + P_mfrr(t)*model.v_r[t]*model.c_r[t])

R_dh = lambda t:  model.g[t,'Boiler']*model.n_d*model.c_d[t]*(1-model.v_r[t])

R_h = lambda t: model.g[t,'Electrolyzer']*model.n_e*model.c_h[t]*(1-model.v_r[t]*model.d_mfrr[t]) 
#R_h = lambda t: model.g[t,'Electrolyzer']*model.n_e*model.c_h[t]*(1-model.v_r[t]*0) 

obj = sum(R_mfrr(t) + R_dh(t) + R_h(t) + R_spot(t) for t in T)

model.obj = Objective(expr = obj,sense=maximize)

### Solve model
Using the optimization software Gurobi, the model is solved.

In [71]:
solver = SolverFactory('gurobi') #Free solver: 'glpk'
#solver.options['Method']=2
solver.options['Threads']=2
solver.options['OptimalityTol'] = 1e-2
#solver.options['Presolve']=2
solver.solve(model) 

{'Problem': [{'Name': 'x87607', 'Lower bound': 1348619.1073729068, 'Upper bound': 1348619.10737295, 'Number of objectives': 1, 'Number of constraints': 140169, 'Number of variables': 87607, 'Number of binary variables': 17520, 'Number of integer variables': 17520, 'Number of continuous variables': 70087, 'Number of nonzeros': 285131, 'Sense': 'maximize'}], 'Solver': [{'Status': 'ok', 'Return code': '0', 'Message': 'Model was solved to optimality (subject to tolerances), and an optimal solution is available.', 'Termination condition': 'optimal', 'Termination message': 'Model was solved to optimality (subject to tolerances), and an optimal solution is available.', 'Wall time': '57.3841438293457', 'Error rc': 0, 'Time': 59.05012917518616}], 'Solution': [OrderedDict([('number of solutions', 0), ('number of solutions displayed', 0)])]}

## Results

In [72]:
print("""
    Wind turbine capacity {0} MW 
    Solar pv capacity {4} MW
    Boiler capacity {1} MW 
    Electrolyzer capacity {2} MW 
    Storage capacity {3}MW"""
      .format(model.p['Wind'].value,
              model.p['Boiler'].value,
              model.p['Electrolyzer'].value,
              model.p['Battery'].value,
              model.p['Solar'].value))


    Wind turbine capacity 0.2773128353395829 MW 
    Solar pv capacity 4.025842651852254 MW
    Boiler capacity 0.0 MW 
    Electrolyzer capacity 0.19575763019511397 MW 
    Storage capacity 0.0MW


In [73]:
model.total_capex = Var(rule=total_capex)
print("""
        Investement       {0:9.0f}
        Spot market       {1:9.0f}
        mFRR market       {2:9.0f}
        Secundary markets {3:9.0f}
        Total             {4:9.0f}
        """.format(pyomo.core.expr.current.evaluate_expression(-total_capex),
                   pyomo.core.expr.current.evaluate_expression(sum(R_spot(t) for t in T )),
                   pyomo.core.expr.current.evaluate_expression(sum(R_mfrr(t) for t in T )),
                   pyomo.core.expr.current.evaluate_expression(sum(R_dh(t)+R_h(t) for t in T )),
                   pyomo.core.expr.current.evaluate_expression(-total_capex + sum(R_spot(t)+R_mfrr(t)+R_dh(t)+R_h(t) for t in T ))
                  ))



        Investement        -1000000
        Spot market          818401
        mFRR market               0
        Secundary markets    530218
        Total                348619
        


In [74]:
fig = go.Figure(go.Pie(labels=['Wind turbines','Solar PV','Boiler','Electrolyzer','Battery'],
                       values=(model.p['Wind'].value,
              model.p['Solar'].value,
              model.p['Boiler'].value,
              model.p['Electrolyzer'].value,
              model.p['Battery'].value)))
fig.show()

In [75]:
fig = go.Figure(go.Pie(labels=['Spot','mFRR','Heating','Hydrogen'],
                       values=[pyomo.core.expr.current.evaluate_expression(sum(R_spot(t) for t in T )),
                              pyomo.core.expr.current.evaluate_expression(sum(R_mfrr(t) for t in T )),
                              pyomo.core.expr.current.evaluate_expression(sum(R_dh(t) for t in T )),
                              pyomo.core.expr.current.evaluate_expression(sum(R_h(t) for t in T ))]))
fig.show()

### Spot market

In [26]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=T,
                    y=[value() for value in model.E_sold.values()],name="Sold energy "))
fig.add_trace(go.Scatter(x=T,
                    y=[-value() for value in model.E_bought.values()],name="Bought energy "))

### Spot price

In [27]:
go.Figure(go.Scatter(x=T,
                    y=[value for value in model.c_s.values()]))

## Revenues

In [28]:
Revenue_mFRR = [pyomo.core.expr.current.evaluate_expression(R_mfrr(t)) for t in T]
Revenue_spot = [pyomo.core.expr.current.evaluate_expression(R_spot(t)) for t in T]
Revenue_h = [pyomo.core.expr.current.evaluate_expression(R_h(t)) for t in T]
Revenue_dh = [pyomo.core.expr.current.evaluate_expression(R_dh(t)) for t in T]
tarrif_paid = [pyomo.core.expr.current.evaluate_expression(model.d[t]*tarrif_sell + (1-model.d[t])*tarrif_buy) for t in T]

In [29]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=T,y=tarrif_paid,name='tarrif'))
fig.add_trace(go.Scatter(x=T,y=Revenue_spot,name='Revenue spot'))
fig.add_trace(go.Scatter(x=T,y=Revenue_mFRR,name='Revenue mFRR'))
fig.add_trace(go.Scatter(x=T,y=Revenue_h,name='Revenue hydrogen'))
fig.add_trace(go.Scatter(x=T,y=Revenue_dh,name='Revenue district heating'))

## Wind and solar availability

In [31]:
fig = go.Figure(go.Scatter(x=T,
                           y=[value for value in model.n_w.values()],name='Wind'),
               layout=dict(yaxis_title='Capacity factor'))
fig.add_trace(go.Scatter(x=T,
                         y=[value for value in model.n_pv.values()],name='Solar'))